# Imports

In [1]:
%load_ext autoreload
%autoreload 2

In [2]:
import pandas as pd
from tqdm import tqdm_notebook, tqdm
from collections import defaultdict
import numpy as np
from caduceus.sparse_vector.sparse_vector import SparseVector
import os
from joblib import load, dump, Parallel, delayed
from torch.utils import data

In [3]:
import matplotlib.pyplot as plt

import torch
import torch.nn as nn
import torch.nn.functional as F

from sklearn.preprocessing import LabelBinarizer
from sklearn.model_selection import StratifiedKFold

In [4]:
device = torch.device('cuda' if torch.cuda.is_available() else 'cpu')

# Data Preparation & Dataset

In [ ]:
from transformers import AutoModelForSequenceClassification, AutoTokenizer
from datasets import load_dataset, get_dataset_config_names
from transformers import DataCollatorWithPadding

def load_gue(add_special_tokens=False):
    model_name = "kuleshov-group/caduceus-ph_seqlen-1k_d_model-256_n_layer-4_lr-8e-3"
    masked_lm_model_path = model_name
    tokenizer = AutoTokenizer.from_pretrained(masked_lm_model_path)
    
    config_names = get_dataset_config_names("leannmlindsey/GUE")
    dataset = load_dataset("leannmlindsey/GUE", name="prom_core_all")
    
    tokenized_dataset = dataset.map(
        lambda examples: tokenizer(examples["sequence"], 
            add_special_tokens=add_special_tokens
        ),
        batched=True
    )
    
    data_collator = DataCollatorWithPadding(tokenizer=tokenizer)
    return tokenizer, dataset, tokenized_dataset, data_collator

tokenizer, dataset, tokenized_dataset, data_collator = load_gue(add_special_tokens=True)

In [6]:
params = {'batch_size':128,
          'num_workers':4,
          'shuffle':True}

loader_train = data.DataLoader(tokenized_dataset['train'], **params)
loader_val = data.DataLoader(tokenized_dataset['dev'], **params)
loader_test = data.DataLoader(tokenized_dataset['test'], **params)

## Модель учитель

Архитектура - Caduceus-Ph

In [7]:
# gue dataset

model_name = "kuleshov-group/caduceus-ph_seqlen-1k_d_model-256_n_layer-4_lr-8e-3"
teacher = AutoModelForSequenceClassification.from_pretrained(model_name, num_labels=2)
teacher.score = nn.Sequential(teacher.score, nn.Softmax(dim=-1))

teacher.load_state_dict(torch.load('caduceus/gue_0.8295-ph-1k.pt'))

The repository for kuleshov-group/caduceus-ph_seqlen-1k_d_model-256_n_layer-4_lr-8e-3 contains custom code which must be executed to correctly load the model. You can inspect the repository content at https://hf.co/kuleshov-group/caduceus-ph_seqlen-1k_d_model-256_n_layer-4_lr-8e-3.
You can avoid this prompt in future by passing the argument `trust_remote_code=True`.

Do you wish to run the custom code? [y/N]  y
The repository for kuleshov-group/caduceus-ph_seqlen-1k_d_model-256_n_layer-4_lr-8e-3 contains custom code which must be executed to correctly load the model. You can inspect the repository content at https://hf.co/kuleshov-group/caduceus-ph_seqlen-1k_d_model-256_n_layer-4_lr-8e-3.
You can avoid this prompt in future by passing the argument `trust_remote_code=True`.

Do you wish to run the custom code? [y/N]  y


Some weights of CaduceusForSequenceClassification were not initialized from the model checkpoint at kuleshov-group/caduceus-ph_seqlen-1k_d_model-256_n_layer-4_lr-8e-3 and are newly initialized: ['score.weight']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.


<All keys matched successfully>

## Модель ученик

Архитектура - Mamba

In [7]:
from transformers import MambaConfig, MambaForCausalLM
import sys

from mamba_lrp.model.mamba_huggingface import ModifiedMambaForCausalLM
from mamba_lrp.model.utils import *
from mamba_lrp.lrp.utils import relevance_propagation
from mamba_lrp.dataset.general_dataset import get_sst_dataset

from hf_mamba_classification import MambaForSequenceClassification # https://github.com/getorca/mamba_for_sequence_classification/blob/main/src/hf_mamba_classification.py

In [8]:
model_path = 'state-spaces/mamba-130m-hf'

id2label = {0: "NEGATIVE", 1: "POSITIVE"}
label2id = {"NEGATIVE": 0, "POSITIVE": 1}

student = MambaForSequenceClassification.from_pretrained(
    model_path, 
    num_labels=2, 
    id2label=id2label, 
    label2id=label2id,
    use_cache=False,  # This needs to be passed when using eval and training Mamba for sequence classification otherwise it will raise an error
    intermediate_size=512,
    hidden_size=256,
    num_hidden_layers=4,
    ignore_mismatched_sizes=True
)
resize_token_embeddings(student, len(tokenizer))
student.lm_head = torch.nn.Linear(256, 2, bias=True)

Some weights of MambaForSequenceClassification were not initialized from the model checkpoint at state-spaces/mamba-130m-hf and are newly initialized: ['classifier.weight']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.
Some weights of MambaForSequenceClassification were not initialized from the model checkpoint at state-spaces/mamba-130m-hf and are newly initialized because the shapes did not match:
- backbone.embeddings.weight: found shape torch.Size([50280, 768]) in the checkpoint and torch.Size([50280, 256]) in the model instantiated
- backbone.layers.0.mixer.A_log: found shape torch.Size([1536, 16]) in the checkpoint and torch.Size([512, 16]) in the model instantiated
- backbone.layers.0.mixer.D: found shape torch.Size([1536]) in the checkpoint and torch.Size([512]) in the model instantiated
- backbone.layers.0.mixer.conv1d.bias: found shape torch.Size([1536]) in the checkpoint and torch.Size([512]) in the model insta

## Train Student

In [23]:
def set_random_seed(seed):
    torch.manual_seed(seed)
    torch.cuda.manual_seed_all(seed)
    torch.backends.cudnn.deterministic = True
    torch.backends.cudnn.benchmark = False

In [77]:
from transformers import Trainer, TrainingArguments
from sklearn.metrics import matthews_corrcoef, f1_score, accuracy_score
import gc
from IPython.display import clear_output
import time

def compute_metrics(predictions, labels):
    predictions = np.argmax(predictions, axis=1)
    return {'accuracy': accuracy_score(labels, predictions),
            'mcc': matthews_corrcoef(labels, predictions),
            'f1': f1_score(labels, predictions)
           }

def distillation_loss(student_logits, teacher_logits, temperature=2.0):
    """
    KL-дивергенция между student и teacher логитами.
    """
    student_log_probs = F.log_softmax(student_logits / temperature, dim=-1)
    teacher_probs = F.softmax(teacher_logits / temperature, dim=-1)
    return F.kl_div(student_log_probs, teacher_probs, reduction='batchmean') * (temperature ** 2)

def train_epoch(student_model, teacher_model, dataloader, optimizer, scheduler=None,
                                    device='cuda', temperature=2.0, alpha=0.5):
    """
    Обучает student модель с использованием дистилляции знаний от teacher модели.

    Args:
        student_model: torch.nn.Module
        teacher_model: torch.nn.Module (в режиме eval, не обучается)
        dataloader: DataLoader с батчами (input_ids, attention_mask, labels)
        optimizer: torch.optim.Optimizer
        device: 'cuda' или 'cpu'
        temperature: температура для сглаживания логитов
        alpha: вес дистилляционной потери (1 - alpha для обычной cross-entropy)
    """
    student_model.train()
    teacher_model.eval()

    total_loss = 0

    for batch in tqdm(dataloader):
        input_ids = torch.stack(batch['input_ids'], dim=1).to(device)
        labels = batch['label'].to(device)

        optimizer.zero_grad()

        with torch.no_grad():
            teacher_logits = teacher_model(input_ids=input_ids).logits

        student_logits = student_model(input_ids=input_ids).logits
        student_logits = nn.Softmax(dim=0)(student_logits)
        
        # Классическая cross-entropy по логитам
        ce_loss = F.cross_entropy(student_logits, labels)

        # Дистилляция
        kd_loss = distillation_loss(student_logits, teacher_logits, temperature)
        
        # Общая потеря
        loss = (1 - alpha) * ce_loss + alpha * kd_loss

        loss.backward()
        optimizer.step()

        total_loss += loss.item()

    return total_loss / len(dataloader)

def test(student_model, teacher_model, dataloader, device='cuda', temperature=2.0, alpha=0.5):

    student_model.eval()
    teacher_model.eval()
    
    f1_log, mcc_log, acc_log, loss_log = [], [], [], []
    
    with torch.no_grad():
        for batch in tqdm(dataloader):
            input_ids = torch.stack(batch['input_ids'], dim=1).to(device)
            labels = batch['label'].to(device)

            teacher_logits = teacher_model(input_ids=input_ids).logits
            student_logits = student_model(input_ids=input_ids).logits
            student_logits = nn.Softmax(dim=0)(student_logits)

            # Классическая cross-entropy по логитам
            ce_loss = F.cross_entropy(student_logits, labels)
            # Дистилляция
            kd_loss = distillation_loss(student_logits, teacher_logits, temperature)
            # Общая потеря
            loss = (1 - alpha) * ce_loss + alpha * kd_loss
            
            metrics = compute_metrics(student_logits.cpu(), labels.cpu())
            
            f1_log.append(metrics['f1'])
            acc_log.append(metrics['accuracy'])
            mcc_log.append(metrics['mcc'])
            loss_log.append(loss.item())
            torch.cuda.empty_cache()
            
    return f1_log, mcc_log, acc_log, loss_log

def plot_history(train_history, valid_history, title, BatchSize, epoch_to_show=20):
    plt.figure(figsize=(epoch_to_show, 4))
    plt.title(title)    
    
    epoch_num = len(valid_history)
    train_history = np.array([None] * (BatchSize * epoch_to_show) + train_history)
    valid_history = np.array([None] * epoch_to_show + valid_history)
    
    plt.plot(np.linspace(epoch_num-epoch_to_show+1, epoch_num+1, (epoch_to_show+1)*BatchSize), 
             train_history[-(epoch_to_show+1)*BatchSize:], c='red', label='train')
    plt.plot(np.linspace(epoch_num-epoch_to_show+1, epoch_num+1, epoch_to_show+1),
                valid_history[-epoch_to_show-1:], c='green', label='test')
    
    plt.ylim((0, 1))
    plt.yticks(np.linspace(0, 1, 11))
    plt.xticks(np.arange(epoch_num-epoch_to_show+1, epoch_num+2), 
              np.arange(epoch_num-epoch_to_show, epoch_num+1).astype(int))
    plt.xlabel('train steps')
    plt.legend(loc='best')
    plt.grid()
    plt.show()
    
def train(student_model, teacher_model, train_loader, val_loader, optimizer, n_epochs,
                                    device='cuda', temperature=2.0, alpha=0.5, scheduler=None):
    best_f1 = 0.
    
    train_f1_log, train_mcc_log, train_acc_log, train_loss_log = [], [], [], []
    val_f1_log, val_mcc_log, val_acc_log, val_loss_log = [], [], [], []
    
    for epoch in range(n_epochs):
        gc.collect()
        torch.cuda.empty_cache() 
        start_time = time.time()
        print("Epoch {} of {}".format(epoch + 1, n_epochs))
        train_loss = train_epoch(student_model, teacher_model, train_loader, opt, scheduler)
        val_f1, val_mcc, val_acc, val_loss = test(student_model, teacher_model, val_loader)
        
        end_time = time.time()
        BatchSize = 1#len(train_loss)
        
        # train_f1_log.extend(train_f1)
        # train_mcc_log.extend(train_mcc)
        # train_acc_log.extend(train_acc)
        train_loss_log.append(train_loss)

        val_f1_log.append(np.mean(val_f1))
        val_mcc_log.append(np.mean(val_mcc))
        val_acc_log.append(np.mean(val_acc))
        val_loss_log.append(np.mean(val_loss))
        
        if val_f1_log[-1] > best_f1:
            best_f1 = val_f1_log[-1]
            torch.save(student_model.state_dict(), f'gue_{epoch}_f1_{best_f1}.pt')
        
        if (epoch % 1) == 0:
            clear_output()
            # plot_history(train_loss_log, val_loss_log,     'Loss',     BatchSize)    
            # plot_history(train_acc_log, val_acc_log, 'Accuracy', BatchSize)
            # plot_history(train_mcc_log, val_mcc_log, 'MCC',      BatchSize)
            # plot_history(train_f1_log, val_f1_log,   'F1',       BatchSize)
            print("Time: ", end_time/60)
            print("Epoch {}: MCC = {:.3}".format(epoch+1, val_mcc_log[-1]))
            print("Epoch {}: F1-score = {:.3}".format(epoch+1, val_f1_log[-1]))
        # with open("metrics", "wb") as fp:   #Pickling
        #     pickle.dump({'train_loss_log':train_loss_log,
        #                 'val_loss_log': val_loss_log,
        #                 'train_f1_log': train_f1_log,
        #                 'val_f1_log': val_f1_log,
        #                 'train_mcc_log': train_mcc_log,
        #                 'val_mcc_log': val_mcc_log}, fp)

    print("Final Accuracy = {:.3}".format(val_acc_log[-1]))
    print("Final F1-score = {:.3}".format(val_f1_log[-1]))
    print("Final MCC-score = {:.3}".format(val_mcc_log[-1]))

    return val_f1_log, val_mcc_log, val_acc_log, val_loss_log

In [82]:
teacher.cuda()
student.cuda()

MambaForSequenceClassification(
  (backbone): MambaModel(
    (embeddings): Embedding(12, 256)
    (layers): ModuleList(
      (0-3): 4 x MambaBlock(
        (norm): MambaRMSNorm(256, eps=1e-05)
        (mixer): MambaMixer(
          (conv1d): Conv1d(512, 512, kernel_size=(4,), stride=(1,), padding=(3,), groups=512)
          (act): SiLU()
          (in_proj): Linear(in_features=256, out_features=1024, bias=False)
          (x_proj): Linear(in_features=512, out_features=80, bias=False)
          (dt_proj): Linear(in_features=48, out_features=512, bias=True)
          (out_proj): Linear(in_features=512, out_features=256, bias=False)
        )
      )
    )
    (norm_f): MambaRMSNorm(256, eps=1e-05)
  )
  (classifier): Linear(in_features=256, out_features=2, bias=False)
  (lm_head): Linear(in_features=256, out_features=2, bias=True)
)

In [62]:
teacher

CaduceusForSequenceClassification(
  (caduceus): Caduceus(
    (backbone): CaduceusMixerModel(
      (embeddings): CaduceusEmbeddings(
        (word_embeddings): Embedding(16, 256)
      )
      (layers): ModuleList(
        (0-3): 4 x Block(
          (mixer): BiMambaWrapper(
            (mamba_fwd): Mamba(
              (in_proj): Linear(in_features=256, out_features=1024, bias=False)
              (conv1d): Conv1d(512, 512, kernel_size=(4,), stride=(1,), padding=(3,), groups=512)
              (act): SiLU()
              (x_proj): Linear(in_features=512, out_features=48, bias=False)
              (dt_proj): Linear(in_features=16, out_features=512, bias=True)
              (out_proj): Linear(in_features=512, out_features=256, bias=False)
            )
            (mamba_rev): Mamba(
              (in_proj): Linear(in_features=256, out_features=1024, bias=False)
              (conv1d): Conv1d(512, 512, kernel_size=(4,), stride=(1,), padding=(3,), groups=512)
              (act): SiLU(

In [86]:
opt = torch.optim.Adam(student.parameters(), lr=1e-3, betas=(0.95, 0.9))

In [59]:
val_f1_log, val_mcc_log, val_acc_log, val_loss_log = train(student, teacher, loader_train, loader_val, opt, 5, alpha=0.8)

Time:  29122066.269212425
Epoch 5: MCC = 0.154
Epoch 5: F1-score = 0.592
Final Accuracy = 0.577
Final F1-score = 0.592
Final MCC-score = 0.154


In [88]:
val_f1_log, val_mcc_log, val_acc_log, val_loss_log = train(student, teacher, loader_train, loader_val, opt, 15, alpha=0.7)

Time:  29122096.84237338
Epoch 15: MCC = 0.557
Epoch 15: F1-score = 0.768
Final Accuracy = 0.777
Final F1-score = 0.768
Final MCC-score = 0.557


# Interpretation of Student

## LRP

In [9]:
student.load_state_dict(torch.load('gue_2_f1_0.791.pt'))

<All keys matched successfully>

In [13]:
student.cuda()

MambaForSequenceClassification(
  (backbone): MambaModel(
    (embeddings): Embedding(12, 256)
    (layers): ModuleList(
      (0-3): 4 x MambaBlock(
        (norm): MambaRMSNorm(256, eps=1e-05)
        (mixer): MambaMixer(
          (conv1d): Conv1d(512, 512, kernel_size=(4,), stride=(1,), padding=(3,), groups=512)
          (act): SiLU()
          (in_proj): Linear(in_features=256, out_features=1024, bias=False)
          (x_proj): Linear(in_features=512, out_features=80, bias=False)
          (dt_proj): Linear(in_features=48, out_features=512, bias=True)
          (out_proj): Linear(in_features=512, out_features=256, bias=False)
        )
      )
    )
    (norm_f): MambaRMSNorm(256, eps=1e-05)
  )
  (classifier): Linear(in_features=256, out_features=2, bias=False)
  (lm_head): Linear(in_features=256, out_features=2, bias=True)
)

In [10]:
modified_model = ModifiedMambaForCausalLM(student, is_fast_forward_available=False)
modified_model.eval()
pretrained_embeddings = student.backbone.embeddings

In [21]:
from captum.attr import visualization as viz

def interpret(seq):
    input_ids = torch.Tensor(seq['input_ids']).unsqueeze(0).long().to(device)
    label = torch.tensor(seq['label']).unsqueeze(0).long().to(device)
    
    embeddings = pretrained_embeddings(input_ids)
    
    R, prediction = relevance_propagation(
        model=modified_model,
        embeddings=embeddings,
        targets=label,
        n_classes=2
    )

    tokens = []
    for id in input_ids[0][: -1]:
        tokens.append(tokenizer.convert_tokens_to_string(tokenizer.convert_ids_to_tokens([id.item()])))
    attributions = R[0][: -1]
    attributions = attributions / attributions.max()
    
    # Visualize the attributions
    viz.visualize_text([viz.VisualizationDataRecord(
        attributions,
        torch.max(student(input_ids).logits, dim=1).values.item(),
        torch.argmax(student(input_ids).logits, dim=1).item(),
        true_class=label.item(),
        attr_class=label.item(),
        attr_score=attributions.sum(),
        raw_input_ids=tokens,
        convergence_score=None
    )])
    return attributions

In [22]:
interpret(tokenized_dataset['dev'][0])

array([ 6.72210334e-03,  2.15818435e-02,  3.86709832e-02, -2.13353261e-02,
        1.01793945e-01,  1.07518800e-01, -3.04763461e-03, -1.64330602e-02,
        6.65676668e-02,  4.84690480e-02,  1.14426471e-01,  1.34323686e-01,
        1.68689638e-01,  1.86531827e-01,  1.45841554e-01,  2.54637092e-01,
        3.64330739e-01,  2.78281188e-03,  1.00265265e-01,  5.58791272e-02,
        1.66581720e-01,  1.03888646e-01,  2.90230047e-02,  7.84010515e-02,
        9.77228582e-02,  2.53225081e-02,  2.12155655e-01,  1.26610205e-01,
        2.77987886e-02, -3.17472965e-02, -9.53893084e-03,  2.23059184e-03,
       -1.71525236e-02, -1.39998337e-02,  2.03353688e-02, -4.45991568e-03,
        2.07689195e-03,  4.04050713e-03, -2.91609243e-02,  3.99324894e-02,
       -1.51179582e-02, -2.00845730e-02, -1.03130294e-02, -3.60995182e-03,
       -1.43598430e-02,  6.18170109e-03, -2.27786135e-02,  1.48677509e-02,
        3.91354263e-02, -2.70854402e-02,  2.21197633e-03, -1.11815082e-02,
        9.99522381e-05,  

In [29]:
attributions = interpret(tokenized_dataset['dev'][2])
attributions

array([-0.03609234, -0.00835373, -0.00382846,  0.00534417,  0.00153251,
        0.01494397,  0.01478018,  0.00198679,  0.00885551,  0.00702265,
        0.00558628,  0.01392846,  0.01200448,  0.01006189,  0.007658  ,
        0.0074113 ,  0.01461757,  0.01269516,  0.01230921,  0.0092136 ,
        0.00960317,  0.02015091,  0.00977878,  0.02145576,  0.02785897,
        0.01579092, -0.0011204 ,  0.03129504,  0.02773942,  0.00921753,
        0.03633547,  0.01452735, -0.01961955,  0.03155735, -0.06700066,
        0.04113669,  0.02057458, -0.00149072,  0.10439104,  0.07376799,
       -0.01259244,  0.03321167, -0.00234799, -0.02270972,  0.07544976,
       -0.08090506, -0.00297617,  0.04621961,  0.03180333,  0.03363496,
        0.05094346,  0.02093089,  0.02530858,  0.00639113,  0.04032256,
        0.05341797,  0.08154644,  0.11904973,  0.05179458,  0.11345383,
        0.17656948,  0.22456512,  0.18765053,  0.24774458,  0.0219623 ,
        0.4937292 ,  1.        ,  0.99354744,  0.3445358 ,  0.72

In [173]:
attributions = interpret(tokenized_dataset['dev'][6])

In [126]:
lrp_scores = []
seqs = []

i = -1
while True:
    i += 1
    if len(lrp_scores) == 300:
        break
    if tokenized_dataset['test'][i]['label'] == 0:
        continue
    with torch.no_grad():
        outputs = student(**tokenizer(tokenized_dataset['test'][i]['sequence'], return_tensors='pt').to(device)).logits.argmax().item
    if outputs == 0:
        continue
    scores = interpret(tokenized_dataset['test'][i])
    lrp_scores.append(scores)
    seqs.append(tokenized_dataset['test'][i])

# [interpret(tokenized_dataset['dev'][i]['label']) for i in range(500)]

In [161]:
def sum_of_windows_np(arr):
    # Создаем 2D массив с окнами размером 7xN, где каждый столбец - это окно
    windows = np.lib.stride_tricks.sliding_window_view(arr[0], window_shape=7)
    
    # Шаг 2: суммируем каждое окно по строкам (оси 1) и возвращаем результат
    window_sums = np.sum(windows[::1, :], axis=1)
    
    return window_sums
    
def top_attr_score(all_scores, all_seqs, k, n_top):

    counts = defaultdict(int)
    score_sums = defaultdict(float)
    
    for scores, seq in zip(all_scores, all_seqs):
        sums = sum_of_windows_np(scores)
        for i, score in enumerate(sums):
            kmer = seq[i:i+k]
            counts[kmer] += 1
            score_sums[kmer] += score
            
    importances = defaultdict(float)
    for key in counts:
        importances[key] = score_sums[key] / counts[key]
        
    result = [(k, v, counts[k]) for k, v in sorted(importances.items(), key=lambda item: item[1])][-n_top:][::-1]
    # print(f'Top-{n_top} most important {k}mers:')
    return result

In [129]:
tp_seqs = []
for seq in seqs:
    tp_seqs.append(seq['sequence'])

In [90]:
mer3 = top_attr_score(lrp_scores[:100], tp_seqs[:100], 3, 5)
mer2 = top_attr_score(lrp_scores[:100], tp_seqs[:100], 2, 5)
mer1 = top_attr_score(lrp_scores[:100], tp_seqs[:100], 1, 5)
top = mer3 + mer2 + mer1
tmp = sorted(top, key=lambda x: -x[1])

kmer, score, cnt = [], [], []
for k, s, c in tmp:
    kmer.append(k)
    score.append(s)
    cnt.append(c)

In [157]:
import pandas as pd
pd.DataFrame({'kmer': kmer, 'Score': score, 'Count': cnt})

kmer     Score  Count
0   GCC  0.080427    184
1   GAG  0.019399    168
2   CTG -0.045958    175
3   TGC -0.094487    136
4   CGG -0.128440    121
5    GC -0.278866    597
6    GG -0.479605    551
7    CC -0.568345    543
8    CA -0.725476    401
9    AG -0.758879    543
10    C -0.790853   1719
11    G -0.802897   1805
12    A -2.130827   1496
13    T -2.427356   1380

## SHAP

In [ ]:
import shap
import transformers

classifier = transformers.pipeline("text-classification", top_k=None, model=student, tokenizer=tokenizer)

In [49]:
explainer = shap.Explainer(classifier, tokenizer)

In [143]:
shap_values = explainer(tp_seqs[:100])

PartitionExplainer explainer: 101it [02:10,  1.41s/it]                          


In [144]:
# model scores for TP sequences
scores = []
for val in shap_values:
    scores.append(val.values[:, 1])

In [154]:
mer3 = top_attr_score(scores, tp_seqs[:100], 3, 5)
mer2 = top_attr_score(scores, tp_seqs[:100], 2, 5)
mer1 = top_attr_score(scores, tp_seqs[:100], 1, 5)
top = mer3 + mer2 + mer1
tmp = sorted(top, key=lambda x: -x[1])

kmer, score, cnt = [], [], []
for k, s, c in tmp:
    kmer.append(k)
    score.append(s)
    cnt.append(c)

In [155]:
import pandas as pd
pd.DataFrame({'kmer': kmer, 'Score': score, 'Count': cnt}) # 100 from test

kmer         Score  Count
0   TTC  2.948153e-08     90
1   GTT  2.786983e-08     80
2   CGT  2.506472e-08     46
3   CCG  2.206902e-08    112
4   CGG  1.400770e-08    123
5    CG  1.009704e-08    322
6    CC  5.040594e-09    553
7    TC  3.203104e-10    346
8    TT  2.908715e-10    349
9    GG -7.183778e-09    562
10    C -1.317293e-08   1752
11    T -2.297389e-08   1396
12    G -2.627308e-08   1831
13    A -8.291045e-08   1521

In [54]:
shap.plots.text(shap_values)

## Integrated Gradients

In [110]:
from transformers_interpret import SequenceClassificationExplainer

cls_explainer = SequenceClassificationExplainer(model=student, tokenizer=tokenizer_trunc)

cls_explainer(text=tokenized_dataset["test"][0]['sequence'])

[('G', 0.0020596207483561993),
 ('C', -0.0003802532383775007),
 ('A', -0.00440157753961326),
 ('A', -0.0029835699811859373),
 ('T', -0.015863297004601894),
 ('A', -0.0008023940074261023),
 ('A', 0.009594203966061544),
 ('A', 0.006107401986125816),
 ('A', -0.010224080398650512),
 ('G', 0.037114302781969664),
 ('G', 0.004887322874535199),
 ('C', 0.019753670172447738),
 ('T', 0.0006453859658875439),
 ('T', 3.0590645925541204e-06),
 ('A', -0.00893307328550077),
 ('G', 0.019276701923606462),
 ('C', -0.000810499025868952),
 ('C', 0.020880984279230262),
 ('A', 0.005710285685256842),
 ('C', 0.010734844904841813),
 ('A', -0.039340951830356685),
 ('T', -0.04388842041396035),
 ('A', -0.03542239763252787),
 ('G', 0.05078919719444281),
 ('T', 0.011144081666473757),
 ('G', 0.02226013829873419),
 ('C', 0.029932931209744426),
 ('A', -0.007395757142623885),
 ('T', -0.0036078280364048045),
 ('G', -0.007698166666664917),
 ('C', -0.013118873566202479),
 ('A', -0.006963222186675395),
 ('G', -0.005301528369

In [111]:
cls_explainer.visualize()

In [159]:
raw_scores = []
i = 0
for data in tqdm(seqs):
    if i == 100:
        break
    i += 1
    
    expl_seq = cls_explainer(text=data['sequence'])
    seq, attr_score = zip(*expl_seq)
    raw_scores.append([attr_score])

 33%|█████████████▋                           | 100/300 [00:04<00:08, 24.89it/s]


In [162]:
mer3 = top_attr_score(raw_scores, tp_seqs[:100], 3, 5)
mer2 = top_attr_score(raw_scores, tp_seqs[:100], 2, 5)
mer1 = top_attr_score(raw_scores, tp_seqs[:100], 1, 5)

top = mer3 + mer2 + mer1
tmp = sorted(top, key=lambda x: -x[1])

kmer, score, cnt = [], [], []
for k, s, c in tmp:
    kmer.append(k)
    score.append(s)
    cnt.append(c)

Top-5 most important 3mers:
Top-5 most important 2mers:
Top-5 most important 1mers:


In [163]:
import pandas as pd
pd.DataFrame({'kmer': kmer, 'Score': score, 'Count': cnt})

kmer     Score  Count
0   CAT  0.099243     65
1   TCG  0.087065     41
2   ATG  0.069443     54
3   GGA  0.068183    133
4   ATT  0.065082     57
5    CC  0.050274    543
6    GA  0.042288    381
7    GG  0.038817    551
8     G  0.030486   1805
9     C  0.028874   1719
10   TC  0.028379    340
11   AG  0.026561    543
12    A  0.022107   1496
13    T  0.019502   1380

# Interpretation of teacher

## Integrated Gradients

In [108]:
from typing import List, Optional, Dict, Sequence, Tuple

from transformers import PreTrainedTokenizer
from transformers_interpret import SequenceClassificationExplainer
from tqdm import tqdm

class CaduceusTokenizerTrunc(PreTrainedTokenizer): # dummy class that removes SEP token from tokenized sequence 
    model_input_names = ["input_ids"]

    def __init__(self,
                 model_max_length: int,
                 characters: Sequence[str] = ("A", "C", "G", "T", "N"),
                 complement_map=None,
                 bos_token="[BOS]",
                 eos_token="[SEP]",
                 sep_token="[SEP]",
                 cls_token="[CLS]",
                 pad_token="[PAD]",
                 mask_token="[MASK]",
                 unk_token="[UNK]",
                 **kwargs):
        """Character tokenizer for Hugging Face transformers.

        Adapted from https://huggingface.co/LongSafari/hyenadna-tiny-1k-seqlen-hf/blob/main/tokenization_hyena.py
        Args:
            model_max_length (int): Model maximum sequence length.
            characters (Sequence[str]): List of desired characters. Any character which
                is not included in this list will be replaced by a special token called
                [UNK] with id=6. Following is a list of the special tokens with
                their corresponding ids:
                    "[CLS]": 0
                    "[SEP]": 1
                    "[BOS]": 2
                    "[MASK]": 3
                    "[PAD]": 4
                    "[RESERVED]": 5
                    "[UNK]": 6
                an id (starting at 7) will be assigned to each character.
            complement_map (Optional[Dict[str, str]]): Dictionary with string complements for each character.
        """
        if complement_map is None:
            complement_map = {"A": "T", "C": "G", "G": "C", "T": "A", "N": "N"}
        self.characters = characters
        self.model_max_length = model_max_length

        self._vocab_str_to_int = {
            "[CLS]": 0,
            "[SEP]": 1,
            "[BOS]": 2,
            "[MASK]": 3,
            "[PAD]": 4,
            "[RESERVED]": 5,
            "[UNK]": 6,
            **{ch: i + 7 for i, ch in enumerate(self.characters)},
        }
        self._vocab_int_to_str = {v: k for k, v in self._vocab_str_to_int.items()}
        add_prefix_space = kwargs.pop("add_prefix_space", False)
        padding_side = kwargs.pop("padding_side", "left")

        self._complement_map = {}
        for k, v in self._vocab_str_to_int.items():
            complement_id = self._vocab_str_to_int[complement_map[k]] if k in complement_map.keys() else v
            self._complement_map[self._vocab_str_to_int[k]] = complement_id

        super().__init__(
            bos_token=bos_token,
            eos_token=eos_token,
            sep_token=sep_token,
            cls_token=cls_token,
            pad_token=pad_token,
            mask_token=mask_token,
            unk_token=unk_token,
            add_prefix_space=add_prefix_space,
            model_max_length=model_max_length,
            padding_side=padding_side,
            **kwargs,
        )

    @property
    def vocab_size(self) -> int:
        return len(self._vocab_str_to_int)

    @property
    def complement_map(self) -> Dict[int, int]:
        return self._complement_map

    def _tokenize(self, text: str, **kwargs) -> List[str]:
        return list(text.upper())  # Convert all base pairs to uppercase

    def _convert_token_to_id(self, token: str) -> int:
        return self._vocab_str_to_int.get(token, self._vocab_str_to_int["[UNK]"])

    def _convert_id_to_token(self, index: int) -> str:
        return self._vocab_int_to_str[index]

    def convert_tokens_to_string(self, tokens):
        return "".join(tokens)  # Note: this operation has lost info about which base pairs were originally lowercase

    def get_special_tokens_mask(
        self,
        token_ids_0: List[int],
        token_ids_1: Optional[List[int]] = None,
        already_has_special_tokens: bool = False,
    ) -> List[int]:
        if already_has_special_tokens:
            return super().get_special_tokens_mask(
                token_ids_0=token_ids_0,
                token_ids_1=token_ids_1,
                already_has_special_tokens=True,
            )

        result = ([0] * len(token_ids_0)) + [1]
        if token_ids_1 is not None:
            result += ([0] * len(token_ids_1)) + [1]
        return result

    def build_inputs_with_special_tokens(
        self, token_ids_0: List[int], token_ids_1: Optional[List[int]] = None
    ) -> List[int]:
        sep = [self.sep_token_id]
        # cls = [self.cls_token_id]
        result = token_ids_0# + sep
        if token_ids_1 is not None:
            result += token_ids_1 + sep
        return result

    def get_vocab(self) -> Dict[str, int]:
        return self._vocab_str_to_int

    # Fixed vocabulary with no vocab file
    def save_vocabulary(self, save_directory: str, filename_prefix: Optional[str] = None) -> Tuple:
        return ()

In [109]:
tokenizer_trunc = CaduceusTokenizerTrunc(
    model_max_length=131072,
    complement_map = tokenizer.complement_map
)

In [43]:
from transformers_interpret import SequenceClassificationExplainer

cls_explainer = SequenceClassificationExplainer(model=teacher, tokenizer=tokenizer_trunc)

cls_explainer(text=tokenized_dataset["test"][0]['sequence'])

[('G', -0.02272874780077807),
 ('C', 0.020332691117615546),
 ('A', -0.019477094306320768),
 ('A', 0.09589136748433773),
 ('T', -0.0599355409352968),
 ('A', 0.05281295133943184),
 ('A', 0.03305630671031337),
 ('A', 0.04089035775597921),
 ('A', 0.09401061757626873),
 ('G', -0.01581770532093722),
 ('G', 0.07625482445372932),
 ('C', -0.2922637637939151),
 ('T', -0.01730136130445904),
 ('T', 0.19015506699283385),
 ('A', 0.0880629834694845),
 ('G', 0.03751968139555241),
 ('C', -0.14580838708043123),
 ('C', -0.2664387000980375),
 ('A', -0.001787385286473923),
 ('C', -0.27507493490571505),
 ('A', 0.10232435821865996),
 ('T', 0.22811316558358752),
 ('A', 0.10842382930436646),
 ('G', -0.14053195709265),
 ('T', -0.000706333359591897),
 ('G', -0.1742380503082306),
 ('C', -0.23884437465317537),
 ('A', 0.11248097342024713),
 ('T', -0.003283601215186013),
 ('G', -0.01684023465526359),
 ('C', -0.2883384708030539),
 ('A', 0.08469908272924048),
 ('G', -0.05970732971595813),
 ('A', -0.0020430762832530825

In [44]:
cls_explainer.visualize()

In [63]:
import numpy as np
npzfile = np.load('caduceus/test_attr_scores_new1.npz')

labels=npzfile['label']
preds=npzfile['pred']
raw_scores=npzfile['raw_scores']

In [69]:
seqs = []
i = 0
for data in tqdm(tokenized_dataset["test"]):
    if i==3777:
        break
    seqs += [data['sequence']]
    i += 1

 64%|██████████████████████▉             | 3777/5920 [00:00<00:00, 25663.60it/s]


In [70]:
tp_seqs = np.array(seqs)[(np.array(labels)==1) & (np.array(preds)==1)]
tp_scores = np.array(raw_scores)[(np.array(labels)==1) & (np.array(preds)==1)]

In [73]:
tp_seqs

array(['GGCTATTTAAGTCAAGGGCCGGCTGGCAACCCCAGCAAGCTGTCCTGTGAGCCGCCAGCATGGATGACAT',
       'GATTACAAATGAGACTGGGAAACCCTCTTCAATAAGACCTGTGTGATGATAGATTGTGTCCTGAGCCCGC',
       'GAGTATATAAGTTCCAGTACCAGCAACAGCAGCAGAAGAAACAACATCTGTTTCAGGGCCATTGGACTCT',
       ...,
       'AGGTGGGACGGCGGCGCGCTGAGGAGGCGGTGCGCTCAGGCGGCGCTCCCGGAGATGCCCCGCGGCAGCC',
       'TTCACGTTGTCCCGTTGAACGTCACTTCCGCTTAGGGGCGGACACGTCCCAAACCTGTGGCGGGAGTTGG',
       'CCCCCGACCCCGCCTCCTCTCCCCCCACCCCTCCTTTCCTCTCCCTCCCCCGCCGAGGCCTGGCTGCCCC'],
      dtype='<U70')

In [181]:
from collections import defaultdict
import numpy as np

def sum_of_windows_np(arr, k):
    # Создаем 2D массив с окнами размером 5xN, где каждый столбец - это окно
    windows = np.lib.stride_tricks.sliding_window_view(arr, window_shape=k)
    
    # Шаг 2: mean каждое окно по строкам (оси 1) и возвращаем результат
    window_sums = np.mean(windows[::1, :], axis=1)
    
    return window_sums
    
def top_attr_score(all_scores, all_seqs, k, n_top):

    counts = defaultdict(int)
    score_sums = defaultdict(float)
    
    for scores, seq in zip(all_scores, all_seqs):
        sums = sum_of_windows_np(scores, k)
        for i, score in enumerate(sums):
            kmer = seq[i:i+k]
            counts[kmer] += 1
            score_sums[kmer] += score
            
    importances = defaultdict(float)
    for key in counts:
        importances[key] = score_sums[key] / counts[key]
        
    result = [(k, v, counts[k]) for k, v in sorted(importances.items(), key=lambda item: item[1])][-n_top:][::-1]
    print(f'Top-{n_top} most important {k}mers:')
    #print(result[0])
    return result

In [111]:
mer3 = top_attr_score(tp_scores, tp_seqs, 3, 5)
mer2 = top_attr_score(tp_scores, tp_seqs, 2, 5)
mer1 = top_attr_score(tp_scores, tp_seqs, 1, 5)

Top-5 most important 3mers:
Top-5 most important 2mers:
Top-5 most important 1mers:


In [112]:
top = mer3 + mer2 + mer1
tmp = sorted(top, key=lambda x: -x[1])

kmer, score, cnt = [], [], []
for k, s, c in tmp:
    kmer.append(k)
    score.append(s)
    cnt.append(c)

In [113]:
import pandas as pd
pd.DataFrame({'kmer': kmer, 'Score': score, 'Count': cnt})

kmer     Score  Count
0   GCG  0.082989   3894
1    GC  0.079525  12850
2   CGC  0.077936   3462
3   CGG  0.072569   3498
4   GCC  0.071867   3958
5   GGC  0.071304   4241
6     G  0.069405  37695
7    CG  0.067275   8978
8    GG  0.057543  12398
9     C  0.057237  35549
10   CC  0.055300  11255
11   TG  0.031639   7034
12    T -0.024295  20727
13    A -0.051997  20549

In [175]:
# to match results with shap:

tmp_scores = np.vstack([tp_scores[:300], tp_scores[-200:]])
tmp_seqs = np.concatenate([tp_seqs[:300], tp_seqs[-200:]])

mer3 = top_attr_score(tmp_scores, tmp_seqs, 3, 5)
mer2 = top_attr_score(tmp_scores, tmp_seqs, 2, 5)
mer1 = top_attr_score(tmp_scores, tmp_seqs, 1, 5)

Top-5 most important 3mers:
Top-5 most important 2mers:
Top-5 most important 1mers:


In [176]:
top = mer3 + mer2 + mer1
tmp = sorted(top, key=lambda x: -x[1])

kmer, score, cnt = [], [], []
for k, s, c in tmp:
    kmer.append(k)
    score.append(s)
    cnt.append(c)

In [177]:
import pandas as pd
pd.DataFrame({'kmer': kmer, 'Score': score, 'Count': cnt})

kmer     Score  Count
0   GCG  0.081281    875
1   CGC  0.074222    800
2    GC  0.071823   3535
3   CGG  0.064753    872
4   GCC  0.063930   1084
5    CG  0.062027   2153
6   CCG  0.061412    770
7     G  0.057628  10775
8     C  0.053403  10254
9    CC  0.048623   3215
10   GG  0.042348   3444
11   CT  0.029320   2558
12    T -0.025113   6729
13    A -0.048073   7242

## SHAP

In [114]:
import shap
import transformers

classifier = transformers.pipeline("text-classification", top_k=None, model=teacher, tokenizer=tokenizer_trunc) # or top_k=1

Device set to use cuda:0


In [115]:
explainer = shap.Explainer(classifier)

In [122]:
import numpy as np
np.savez('tp_seqs.npz', tp_seq=tp_seqs)

In [147]:
shap_values = explainer(tp_seqs[0:300])
shap_scores = shap_values[:, :, 'LABEL_1'].values[:,:70]

all_shap_scores = np.vstack([all_shap_scores, shap_scores])

PartitionExplainer explainer: 151it [05:09,  2.12s/it]                          


In [155]:
shap_values = explainer(tp_seqs[-200:])
shap_scores = shap_values[:, :, 'LABEL_1'].values[:,:70]

PartitionExplainer explainer: 201it [06:49,  2.09s/it]                          


In [156]:
top_attr_score(shap_scores, tp_seqs[-200:], 3, 8)

Top-8 most important 3mers:


[('GGG', 0.003356151090107915, 476),
 ('CGG', 0.0028650444784636777, 448),
 ('TTT', 0.002653445934672126, 170),
 ('CCG', 0.0023996710436010936, 409),
 ('CCC', 0.0023600335443187985, 432),
 ('GCC', 0.0016350185272009862, 495),
 ('GGC', 0.0015769195227130401, 527),
 ('GCG', 0.0014734388901906205, 442)]

In [157]:
all_shap_scores = np.vstack([all_shap_scores, shap_scores])
np.savez('tp_shap_scores.npz', scores=all_shap_scores)

In [182]:
mer3 = top_attr_score(all_shap_scores, tmp_seqs, 3, 5)
mer2 = top_attr_score(all_shap_scores, tmp_seqs, 2, 5)
mer1 = top_attr_score(all_shap_scores, tmp_seqs, 1, 5)

top = mer3 + mer2 + mer1
tmp = sorted(top, key=lambda x: -x[1])

kmer, score, cnt = [], [], []
for k, s, c in tmp:
    kmer.append(k)
    score.append(s)
    cnt.append(c)

Top-5 most important 3mers:
Top-5 most important 2mers:
Top-5 most important 1mers:


In [185]:
import pandas as pd
pd.DataFrame({'kmer': kmer, 'Score': score, 'Count': cnt})

kmer     Score  Count
0   GGG  0.004029   1032
1   CGG  0.003227    872
2    GG  0.003215   3444
3   CCG  0.003078    770
4   TTT  0.002850    459
5   CCC  0.002093    933
6    CG  0.001814   2153
7    CC  0.001162   3215
8     G  0.000295  10775
9    TT -0.000420   1525
10   GC -0.001236   3535
11    C -0.002304  10254
12    T -0.005507   6729
13    A -0.015580   7242